In [1]:
from shapely.geometry import Point 
from shapely.geometry import LineString
import pandas as pd
import geopandas as gpd
import sys
import matplotlib.pyplot as plt
import datetime as datetime
import numpy as np
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from folium import plugins
from folium.plugins import HeatMap
from folium.plugins import HeatMapWithTime

# Adding csv data

In [2]:
tornado_911 = pd.read_csv('../data/911_Phone_Calls_Tornado_030320.csv')
cadd_tornado = pd.read_csv('../data/Computer_Aided_Dispatch_Data_Tornado_Incidents_030320.csv', skiprows = 3)
derecho_911 = pd.read_csv('../data/911_Phone_Calls_Derecho_050320_050420.csv')
cadd_derecho = pd.read_csv('../data/Computer_Aided_Dispatch_Data_Derecho_Incidents_050320-050420.csv', skiprows = 3)

# Fixing columns

In [3]:
tornado_911.columns = ['time', 'calltype', 'lat', 'lng', 'cell_tower_address']
derecho_911.columns = ['time', 'calltype', 'lat', 'lng', 'cell_tower_address']
cadd_tornado.columns = ['time', 'location', 'lat', 'lng', 'incident_type']
cadd_derecho.columns = ['time', 'location', 'lat', 'lng', 'incident_type']

In [4]:
tornado_911.time = pd.to_datetime(tornado_911.time)
derecho_911.time = pd.to_datetime(derecho_911.time)
cadd_tornado.time = pd.to_datetime(cadd_tornado.time)
cadd_derecho.time = pd.to_datetime(cadd_derecho.time)

In [5]:
tornado_911 = tornado_911.dropna(subset = ['lat', 'lng'])
derecho_911 = derecho_911.dropna(subset = ['lat', 'lng'])
cadd_tornado = cadd_tornado.dropna(subset = ['lat', 'lng'])
cadd_derecho = cadd_derecho.dropna(subset = ['lat', 'lng'])

In [6]:
tornado_911['geometry'] = tornado_911.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)
derecho_911['geometry'] = derecho_911.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)
cadd_tornado['geometry'] = cadd_tornado.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)
cadd_derecho['geometry'] = cadd_derecho.apply(lambda x: Point((float(x.lng), float(x.lat))), axis=1)

### Check them here

In [7]:
#tornado_911.head()

In [8]:
#derecho_911.head()

In [9]:
#cadd_tornado.head()

In [10]:
#cadd_derecho.head()

# Breaking down the dataframes by time

### For Tornado 911 Calls

In [11]:
tornado_911['count'] = 1
tornado_911['minute'] = tornado_911['time'].dt.minute
torn_count = pd.DataFrame(
            tornado_911.groupby(['cell_tower_address', 'lat', 'lng'])\
            ['count'].sum().sort_values(ascending = False))

tornado_list = torn_count.groupby(
            ['lat', 'lng'])\
            .sum().reset_index().values.tolist()

In [12]:
torn_minute_list = []

for minute in tornado_911['minute'].sort_values().unique():
    torn_minute_list.append(tornado_911.loc[tornado_911['minute'] == minute,
    ['lat', 'lng', 'count']]\
    .groupby(['lat', 'lng'])\
    .sum().reset_index().values.tolist())
                          
torn_minute_list

[[[36.04139, -86.660929, 1.0],
  [36.154633, -86.7845, 1.0],
  [36.165158, -86.780362, 1.0],
  [36.169825, -86.812956, 1.0],
  [36.17505, -86.814716, 1.0],
  [36.17535, -86.804756, 1.0],
  [36.176316, -86.745815, 1.0],
  [36.176509, -86.754527, 1.0],
  [36.176723, -86.812613, 1.0],
  [36.178215, -86.692278, 1.0],
  [36.182045, -86.74927, 1.0],
  [36.186989, -86.628052, 1.0],
  [36.189212, -86.757231, 1.0],
  [36.194843, -86.729057, 1.0]],
 [[36.062815, -86.724615, 1.0],
  [36.167412, -86.779953, 1.0],
  [36.175522, -86.74206, 1.0],
  [36.176357, -86.746094, 1.0],
  [36.179211, -86.754593, 1.0],
  [36.183558, -86.610868, 1.0],
  [36.183674, -86.624687, 1.0]],
 [[36.139206, -86.810829, 1.0],
  [36.163021, -86.776802, 1.0],
  [36.167572, -86.780235, 1.0],
  [36.176412, -86.69627, 1.0],
  [36.177914, -86.802249, 1.0],
  [36.189213, -86.757233, 1.0],
  [36.191463, -86.602051, 1.0],
  [36.198429, -86.766953, 1.0],
  [36.199715, -86.619987, 1.0]],
 [[36.167443, -86.791735, 1.0],
  [36.17197, 

In [13]:
torn_count

count
cell_tower_address                    lat       lng              
907 12TH AV N - N                     36.167431 -86.796860      6
1051 B CHICAMAUGA AVE - S Sector      36.185047 -86.748260      3
254 RIVERSIDE DR - SE                 36.174385 -86.727081      3
4914 OLD HICKORY BLVD - S Sector      36.199738 -86.620071      3
254 RIVERSIDE DR - N                  36.174404 -86.727081      3
...                                                           ...
2955 BRICK CHURCH PKWY - N SECTOR     36.245377 -86.770878      1
2955 BRICK CHURCH PARKWAY - SE SECTOR 36.221709 -86.768131      1
2817 LEALTO CT - SECTOR SE            36.174747 -86.669212      1
2817 LEALTO CT - SECTOR N             36.181219 -86.675520      1
WIRELESS CALLER                       36.311102 -86.707213      1

[427 rows x 1 columns]

In [14]:
torn_check = tornado_911.groupby(by=[pd.Grouper(key = 'time', freq='1h'), "calltype"]).count().reset_index()
torn_check

time   calltype  lat  lng  cell_tower_address  geometry  \
0 2020-03-03 00:00:00  911 Calls   93   93                  93        93   
1 2020-03-03 01:00:00  911 Calls  187  187                 187       187   
2 2020-03-03 02:00:00  911 Calls   80   80                  80        80   
3 2020-03-03 03:00:00  911 Calls   45   45                  45        45   
4 2020-03-03 04:00:00  911 Calls   45   45                  45        45   

   count  minute  
0     93      93  
1    187     187  
2     80      80  
3     45      45  
4     45      45

In [15]:
midnight_torn_calls = tornado_911[tornado_911.time < '2020-03-03 01:00:00']
one_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 00:59:59') & (tornado_911.time < '2020-03-03 02:00:00')]
two_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 01:59:59') & (tornado_911.time < '2020-03-03 03:00:00')]
three_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 02:59:59') & (tornado_911.time < '2020-03-03 04:00:00')]
four_am_torn_calls = tornado_911[(tornado_911.time > '2020-03-03 03:59:59') & (tornado_911.time < '2020-03-03 05:00:00')]

### For CADD Tornado Responses

In [16]:
cadd_tornado_count = cadd_tornado
cadd_tornado_count['count'] = 1
cadd_torn_check = cadd_tornado_count.groupby(by=[pd.Grouper(key = 'time', freq='1h'), 'count']).count().reset_index()
cadd_torn_check

time  count  location  lat  lng  incident_type  geometry
0 2020-03-03 00:00:00      1        44   44   44             44        44
1 2020-03-03 01:00:00      1        85   85   85             85        85
2 2020-03-03 02:00:00      1        69   69   69             69        69
3 2020-03-03 03:00:00      1        31   31   31             31        31
4 2020-03-03 04:00:00      1        31   31   31             31        31

In [17]:
midnight_cadd_torn_calls = cadd_tornado[cadd_tornado.time < '2020-03-03 01:00:00']
one_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 00:59:59') & (cadd_tornado.time < '2020-03-03 02:00:00')]
two_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 01:59:59') & (cadd_tornado.time < '2020-03-03 03:00:00')]
three_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 02:59:59') & (cadd_tornado.time < '2020-03-03 04:00:00')]
four_am_cadd_torn_calls = cadd_tornado[(cadd_tornado.time > '2020-03-03 03:59:59') & (cadd_tornado.time < '2020-03-03 05:00:00')]

### For Derecho 911 Calls

In [18]:
derecho_911_check = derecho_911
derecho_911_check['count'] = 1
derecho_911_check = derecho_911_check.groupby(by=[pd.Grouper(key = 'time', freq='30min'), 'calltype']).count().reset_index()
derecho_911_check

time   calltype  lat  lng  cell_tower_address  geometry  \
0  2020-05-03 16:30:00  911 Calls  138  138                 138       138   
1  2020-05-03 17:00:00  911 Calls  110  110                 110       110   
2  2020-05-03 17:30:00  911 Calls  146  146                 146       146   
3  2020-05-03 18:00:00  911 Calls  148  148                 148       148   
4  2020-05-03 18:30:00  911 Calls  188  188                 188       188   
5  2020-05-03 19:00:00  911 Calls  151  151                 151       151   
6  2020-05-03 19:30:00  911 Calls  108  108                 108       108   
7  2020-05-03 20:00:00  911 Calls  111  111                 111       111   
8  2020-05-03 20:30:00  911 Calls   76   76                  76        76   
9  2020-05-03 21:00:00  911 Calls   63   63                  63        63   
10 2020-05-03 21:30:00  911 Calls   56   56                  56        56   
11 2020-05-03 22:00:00  911 Calls   75   75                  75        75   
12 2020-05-03 22:30:00  911 Calls   50   50                  50        50   
13 2020-05-03 23:00:00  911 Calls   24   24                  24        24   
14 2020-05-03 23:30:00  911 Calls   23   23                  23        23   
15 2020-05-04 00:00:00  911 Calls   16   16                  16        16   

    count  
0     138  
1     110  
2     146  
3     148  
4     188  
5     151  
6     108  
7     111  
8      76  
9      63  
10     56  
11     75  
12     50  
13     24  
14     23  
15     16

# Adding geojson data

In [19]:
damage_points = gpd.read_file('../data/damage_points.geojson')
path_polygons = gpd.read_file('../data/path_polygons.geojson')
tornado_paths = gpd.read_file('../data/tornado_paths.geojson')

# Fixing columns

In [20]:
damage_points.stormdate = damage_points.stormdate.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
damage_points.surveydate = damage_points.surveydate.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
tornado_paths.stormdate = tornado_paths.stormdate.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
tornado_paths.starttime = tornado_paths.starttime.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))
tornado_paths.endtime = tornado_paths.endtime.apply(lambda x: datetime.datetime.fromtimestamp(x / 1e3))

### Check them here

In [97]:
damage_points.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [22]:
#path_polygons.head()

In [23]:
#tornado_paths

# Making GeoDataFrames

In [24]:
geo_tornado_911 = gpd.GeoDataFrame(tornado_911, crs = tornado_paths.crs, geometry = tornado_911.geometry)
geo_derecho_911 = gpd.GeoDataFrame(derecho_911, crs = tornado_paths.crs, geometry = derecho_911.geometry)
geo_cadd_tornado = gpd.GeoDataFrame(cadd_tornado, crs = tornado_paths.crs, geometry = cadd_tornado.geometry)
geo_cadd_derecho = gpd.GeoDataFrame(cadd_derecho, crs = tornado_paths.crs, geometry = cadd_derecho.geometry)

# Filtering for the Nashville Tornado

In [95]:
nashville_tornado = tornado_paths.loc[tornado_paths.event_id == 'Nashville']
nashville_path = path_polygons.geometry.iloc[np.r_[4, 10:25, 26:35]]
nashville_path = nashville_path.reset_index()
nashville_path = nashville_path.drop(columns = ['index'])
nashville_damage = gpd.sjoin(damage_points, nashville_path, how = 'inner', op = 'within')
nashville_damage = nashville_damage.drop_duplicates(keep = 'first', subset = ['objectid'])

In [96]:
nashville_damage.shape

(2927, 28)

### Check them here

In [26]:
#nashville_tornado

In [27]:
#nashville_path

In [28]:
#nashville_damage.head()

# Mapping the Nashville Tornado

### Calls

In [29]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_calls = folium.Map(location = startloc, zoom_start = 10)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_calls)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_calls)

for row_index, row_values in midnight_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'red', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in one_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'orange', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in two_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'green', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in three_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'darkblue', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
for row_index, row_values in four_am_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'purple', icon = 'phone', prefix = 'fa')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_calls)
    
map_calls

### CADD Response

In [30]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_cadd_res = folium.Map(location = startloc, zoom_start = 10)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_cadd_res)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_cadd_res)

for row_index, row_values in midnight_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'red')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in one_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'orange')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in two_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'green')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in three_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'darkblue')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
for row_index, row_values in four_am_cadd_torn_calls.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = [row_values['time']]
    icon = folium.Icon(color = 'purple')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(map_cadd_res)
    
map_cadd_res

### Damage

In [31]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_damage = folium.Map(location = startloc, zoom_start = 10)

marker_cluster = MarkerCluster().add_to(map_damage)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_damage)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_damage)

    
for row_index, row_values in nashville_damage.iterrows():
    loc = [row_values['lat'], row_values['lon']]
    pop = 'Happened on: ' + str(row_values['stormdate']) + '. Surveyed on: ' + str(row_values['surveydate']) + '. Damage Caused: ' + str(row_values['damage_txt']) + ' ' + str(row_values['dod_txt']) + '. This caused ' + str(row_values['injuries']) + ' injuries and ' + str(row_values['deaths']) + ' deaths.'
    icon = folium.Icon(color = 'orange')
    marker = folium.Marker(location = loc, popup = pop, icon = icon)
    marker.add_to(marker_cluster)


map_damage

### Heatmap Attempts

In [86]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_heat = folium.Map(location = startloc, zoom_start = 10)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_heat)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_heat)

start = datetime.datetime(2020, 3, 3, 0)
end = datetime.datetime(2020, 3, 3, 6)
daterange = pd.date_range(start = start, end = end, periods = 24)

time_index = [d.strftime('%I:%M %p') for d in daterange]

HeatMapWithTime(torn_minute_list, radius = 30,
               gradient={0.1: 'blue', 0.5: 'lime', 0.75: 'orange', 1: 'red'}, 
                min_opacity=0.4, 
                max_opacity=0.8, 
                use_local_extrema=True)\
                .add_to(map_heat)

map_heat

In [76]:
style = {'fillColor': 'red', 'color': 'red'}
style2 = {'fillColor': 'lightgreen', 'color': 'lightgreen'}
startloc = [36.1627, -86.7816]

map_heat2 = folium.Map(location = startloc, zoom_start = 10)

folium.GeoJson(nashville_tornado.geometry, style_function = lambda x:style).add_to(map_heat2)
folium.GeoJson(nashville_path.geometry, style_function = lambda x:style2).add_to(map_heat2)

HeatMapWithTime(torn_minute_list, radius=20, auto_play=True, position='bottomright',
                name="cluster", max_opacity=0.7).add_to(map_heat2)

map_heat2

In [90]:
nashville_damage.stormdate.max()

Timestamp('2020-03-03 01:34:00')

In [91]:
tornado_paths

objectid                 event_id           stormdate           starttime  \
0    879879                Nashville 2020-03-03 00:32:00 2020-03-03 00:32:00   
1    879077  Hwy 69 Ballpark Tornado 2020-03-03 06:04:00 2020-03-03 06:04:00   
2    879081           Lawley Tornado 2020-03-03 06:28:00 2020-03-03 06:28:00   
3    879877               Cookeville 2020-03-03 01:48:00 2020-03-03 01:48:00   
4    879878                  Goffton 2020-03-03 02:05:00 2020-03-03 02:05:00   
5    879880               Cumberland 2020-03-03 02:25:00 2020-03-03 02:25:00   
6    888677           Buffalo Valley 2020-03-03 01:38:00 2020-03-03 01:38:00   

              endtime  startlat  startlon   endlat   endlon   length  ...  \
0 2020-03-03 01:35:00   36.1725  -86.9478  36.1532 -85.8860  60.1317  ...   
1 2020-03-03 06:12:00   32.6846  -87.6226  32.6863 -87.5492   4.3400  ...   
2 2020-03-03 06:38:00   32.8648  -87.0496  32.8646 -86.9432   6.2100  ...   
3 2020-03-03 01:56:00   36.1715  -85.6628  36.1709 -85.5135   8.3900  ...   
4 2020-03-03 02:06:00   36.1075  -85.4461  36.1068 -85.4420   0.2300  ...   
5 2020-03-03 02:35:00   36.1399  -85.0401  36.1243 -84.8619  10.0700  ...   
6 2020-03-03 01:42:00   36.1602  -85.8055  36.1711 -85.7479   3.3233  ...   

   propdamage  edit_user  edit_time created_user   created_date  \
0         -99       None       None      DATians  1583461561000   
1         -99       None       None      DATians  1583353305000   
2         -99       None       None      DATians  1583357522000   
3      100000       None       None      DATians  1583461208000   
4         -99       None       None      DATians  1583461360000   
5         -99       None       None      DATians  1583534817000   
6         -99       None       None      DATians  1586271666000   

  last_edited_user  last_edited_date  \
0       dat_editor     1618703241000   
1          DATians     1583358165000   
2          DATians     1583359203000   
3          DATians     1590771008000   
4          DATians     1590604073000   
5          DATians     1590605084000   
6          DATians     1598799052000   

                                            comments  Shape__Length  \
0  An historic, long-track, strong EF-3 tornado b...       1.071075   
1                                               None       0.074159   
2                                               Path       0.106695   
3  An historic, violent EF-4 tornado began in wes...       0.149870   
4  A very brief and weak EF-0 tornado touched dow...       0.004130   
5  An EF-2 tornado touched down near the intersec...       0.179387   
6  An EF-0 tornado touched down near the Smith/Pu...       0.058826   

                                            geometry  
0  LINESTRING (-86.94783 36.17249, -86.94461 36.1...  
1  LINESTRING (-87.62263 32.68464, -87.62182 32.6...  
2  LINESTRING (-87.04956 32.86476, -87.04019 32.8...  
3  LINESTRING (-85.66285 36.17151, -85.61103 36.1...  
4  LINESTRING (-85.44610 36.10746, -85.44203 36.1...  
5  LINESTRING (-85.04006 36.13989, -85.03400 36.1...  
6  LINESTRING (-85.80550 36.16017, -85.79778 36.1...  

[7 rows x 29 columns]